In [1]:
import spacy
from spacy.tokens import DocBin
import srsly


- load text to NLP object --> ret DOC object
- create **all** SPAN objects on generated DOC object (``char_span`` --> start, end, label)
- collect all spans in list
- add list as dictionary entry with key ``"sc"`` in ``doc.spans`` --> ``doc.spans["sc"]``

In [6]:
PATH_ANNOTATED_DATA = './annotated/2023_12_20/20231220.jsonl'
PATH_WHOLE_DATA = './annotated/2023_12_20/231220_whole.spacy'
PATH_TRAINING_DATA = './annotated/2023_12_20/231220_train.spacy'
PATH_DEV_DATA = './annotated/2023_12_20/231220_dev.spacy'

In [7]:
# seeding random number generation
import random
random.seed(42)

# load data
data = srsly.read_jsonl(PATH_ANNOTATED_DATA)

# load model
nlp = spacy.load('de_core_news_lg')

# collect annotated DOC objects
docs_all = list()

# iterate over whole dataset
for entry in data:
    # generate doc
    doc = nlp(entry['text'])
    
    # extract associated spans
    spans = list()
    labels = entry['label']
    for label in labels:
        start, end, cat = label
        span = doc.char_span(start, end, label=cat, alignment_mode='expand')
        # catch error where no span was found
        if span is None:
            raise ValueError(f"No correct span found. {doc.text=}, {start=}, {end=}, {label=}")
        
        spans.append(span)

    doc.spans['sc'] = spans
    docs_all.append(doc)

In [8]:
docs_all

[Tägliche Wartungstätigkeiten nach Vorgabe des Maschinenherstellers,
 Wöchentliche Sichtkontrolle Reinigung,
 Tägliche Überprüfung der Ölabscheider,
 Wöchentliche Kontrolle der WC-Anlagen,
 Halbjährliche Kontrolle des Stabbreithalters,
 Brandschutztechnische Prüfung,
 Prüfung von Scharniere Dichtung Schließvorrichtung Schloß Beschlag allgemeine Funktion Schmierung Festhaltevorrichtung,
 Täglicher Technikrundgang,
 Monatliche Sichtkontrolle,
 Monatliche Prüfung von Scharniere Dichtung Schließvorrichtung Schloß Beschlag allgemeine Funktion Schmierung Festhaltevorrichtung,
 Tägliche Kontrolle der Kompressorstationen,
 Tägliche Kesselhauskontrolle,
 Tägliche Kontrolle der Wasseraufbereitungsanlagen,
 Tägliche Kontrolle der Heizungsanlagen,
 Jährliche Überprüfung der Leitern,
 Tägliche Kontrolle Druckkontrolle 4,5 bar 0,5 bar gegebenenfalls Filter sauber machen.,
 Wöchentliche Sichtprüfung Reinigung,
 Betriebssicherheitsüberprüfung,
 Analyse von: Kesselwasser Speisewasser Kondensat Wasserve

In [10]:
spacy.displacy.render(docs_all[-50], style="span")

In [11]:
doc_bin = DocBin(docs=docs_all)
doc_bin.to_disk(PATH_WHOLE_DATA)

**Train/Dev split**

In [12]:
DEV_PART = 0.2
dev_entries = int(DEV_PART * len(docs_all))

# random sampling
train_set = docs_all.copy()
dev_set = [train_set.pop(random.randrange(len(train_set))) for _ in range(dev_entries)]
print(f"Number entries:\n training={len(train_set)}, dev={len(dev_set)}")

Number entries:
 training=216, dev=54


In [13]:
doc_bin_train = DocBin(docs=train_set)
doc_bin_train.to_disk(PATH_TRAINING_DATA)

doc_bin_dev = DocBin(docs=dev_set)
doc_bin_dev.to_disk(PATH_DEV_DATA)

### Test for consistency of saving format by check of retrieval functionality

In [73]:
doc_bin = DocBin().from_disk(PATH_TRAINING_DATA)
docs = list(doc_bin.get_docs(nlp.vocab))

In [77]:
spacy.displacy.render(docs[-4], style="span")

#### *RETRIEVAL SUCCESSFUL*